# Homework 2

In [1]:
from fastai.text.all import *
from torch import nn

## Porblem 1 (25 ponits): Deep Learning Basics

### Note: You can only use tensors for this problem.

In [ ]:
path = untar_data(URLs.MNIST)
Path.BASE_PATH = path
path.ls()

In [ ]:
(path/'training').ls().sorted()

In [ ]:
(path/'testing').ls().sorted()

### 1a (10 points). Create a 'typical' digit for each by averaging and classify the test data with them. Report your overall accuracy. 

### 1b (10 points). Create a NN to classify digits (trained with regular SGD). Note that:
- Since you deal with 10 categories here, it is preferrable to use cross entropy loss.
- Again, anything other than tensors are not allowed in this problem so build your NN from scratch.

### 1c (5 points). Implement your own:
- SGD with Momemtum
- RMSProp

by using two more tensors to tracked the smoothed gradients and L2 norms, respectively. Re-train your model on them and report performance.

## Problem 2 (25 points): Getting Your Data Ready For a NN Language Model

In [ ]:
path = untar_data(URLs.HUMAN_NUMBERS)
Path.BASE_PATH = path
path.ls()

In [ ]:
lines = [line for p in path.ls()[::-1] for line in p.read_text().split(' \n')]
text = ' . '.join([l for l in lines])
text[:1000]

### 2a (5 points). Split **text** by space to get **tokens** and create a **vocab** with unique **tokens**.

In [ ]:
tokens = [t for t in text.split(' ')]
vocab = list(np.unique(tokens))
vocab

### 2b (5 points). Create a mapping from word to indices and convert **tokens** into **nums**, which is a list of indices.

In [ ]:
word2idx = lambda v: [[v.index(n) for n in line.split(' ')] for line in lines] 
nums = word2idx(vocab)
nums

### 2c (5 points). Create a _dataset_ where each tuple is the input and output of a NN language model. The sequence length of inputs and outputs should be 32. Then create a _training set_ with the first 80% data and a _validation set_ with the rest.

In [ ]:
dset = [i+([0]*(16-len(i))) for i in nums]
random.shuffle(dset)
train_ds = np.asarray(dset[:int(len(dset)*.8)])
valid_ds = np.asarray(dset[int(len(dset)*.8):])

### 2d (10 points). Reorder your training set and validation set to be ready for _dataloaders_ to be used in a NN language model. Note that:
- `m = len(dset) // 64` batches will be created in the new order without shuffling (the first 64 rows will be the first batch, the next 64 rows will be the second batch, and so on).
- The new first 64 rows should be the `1st, (1+m)-th, (1+2m)-th, ..., (1+64m)-th` rows in the original corresponding dataset; The next 64 rows should be the `2nd, (2+m)-th, (2+2m)-th, ..., (2+64m)-th` rows; and so on.

In [ ]:
train_ds_reordered = np.array_split(train_ds, 64) 
valid_ds_reordered = np.array_split(valid_ds, 64)

In [ ]:
np.shape(train_ds_reordered)

In [ ]:
dls = DataLoaders.from_dsets(
    train_ds_reordered,
    valid_ds_reordered,
    bs=64, drop_last=True, shuffle=False
)

In [ ]:
next(iter(dls[0]))

## Problem 3 (25 points): Simple NN Language Model

### 3a (15 points). The stacked/unrolled representation depict the same 2-layer RNN. Implement this RNN with only:
- torch.tensor
- tensor functions (from torch.tensor or torch)
- torch.nn.Embedding
- torch.nn.Linear
- torch.nn.relu

<img alt="2-layer RNN" width="550" caption="2-layer RNN" src="./att_00025.png">

<img alt="2-layer unrolled RNN" width="550" caption="Two-layer unrolled RNN" src="./att_00026.png">

### 3b (10 points). Find the best learning rate and train your NN with 1cycle policy and Adam (using _Learner_ class from fastai). Report your result with a reasonable metric.

## Problem 4 (25 points):

### 4a (10 points). Reuse the IMDB reviews dataset from Homework 1. Tokenize (experiment with the vocab size yourself) it with the subword tokenizer you developed in Homework 1 and create _Dataloaders_ in the similar way of Problem 2 to get ready for a LSTM Language Model.

In [2]:
path = untar_data(URLs.IMDB_SAMPLE)
df = pd.read_csv(path/'texts.csv')
df.head()

label  \
0  negative   
1  positive   
2  negative   
3  positive   
4  negative   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      text  \
0                                                                                                                                                                                                    Un-bleeping-believable! Meg Ryan doesn't even look her usual pert lovable self in this, which normally makes me forgive her shallow ticky acting schtick. Hard to believe she was the producer on this dog. Plus Kevin Kline: what kind of suicide trip has his career been on? Whoosh... Banzai!!! Finally this was directed by the guy who did Big Chill? Must be a replay of Jonestown - hollywood style. Wooofff!   
1  This is a extremely well-made film. The acting, script and camera-work are all first-rate. The music is good, too, though it is mostly early in the film, when things are still relatively cheery. There are no really superstars in the cast, though several faces will be familiar. The entire cast does an excellent job with the script.<br /><br />But it is hard to watch, because there is no good end to a situation like the one presented. It is now fashionable to blame the British for setting Hindus and Muslims against each other, and then cruelly separating them into two countries. There is som...   
2  Every once in a long while a movie will come along that will be so awful that I feel compelled to warn people. If I labor all my days and I can save but one soul from watching this movie, how great will be my joy.<br /><br />Where to begin my discussion of pain. For starters, there was a musical montage every five minutes. There was no character development. Every character was a stereotype. We had swearing guy, fat guy who eats donuts, goofy foreign guy, etc. The script felt as if it were being written as the movie was being shot. The production value was so incredibly low that it felt li...   
3  Name just says it all. I watched this movie with my dad when it came out and having served in Korea he had great admiration for the man. The disappointing thing about this film is that it only concentrate on a short period of the man's life - interestingly enough the man's entire life would have made such an epic bio-pic that it is staggering to imagine the cost for production.<br /><br />Some posters elude to the flawed characteristics about the man, which are cheap shots. The theme of the movie "Duty, Honor, Country" are not just mere words blathered from the lips of a high-brassed offic...   
4  This movie succeeds at being one of the most unique movies you've seen. However this comes from the fact that you can't make heads or tails of this mess. It almost seems as a series of challenges set up to determine whether or not you are willing to walk out of the movie and give up the money you just paid. If you don't want to feel slighted you'll sit through this horrible film and develop a real sense of pity for the actors involved, they've all seen better days, but then you realize they actually got paid quite a bit of money to do this and you'll lose pity for them just like you've alr...   

   is_valid  
0     False  
1     False  
2     False  
3     False  
4     False

In [3]:
df.text = [re.sub(r"\<br \/\>", "", i) for i in df.text]

In [4]:
def replacements(x):
    def replace_uppercase(match_object): return match_object.group(0).lower()
    x = re.sub(r"[A-Z]", replace_uppercase, x)
    x = re.sub(r"[.,\/#!$%\^&\*;:{}=\-_`~()\"\?]", " ", x)
    x = re.sub(r"(n\'t)", " not", x)
    x = re.sub(r"(\'ve)", " have", x)
    x = re.sub(r"(\won't)", " would not", x)
    x = re.sub(r"(\'ll)", " will", x)
    x = re.sub(r"(\'re)", " are", x)
    x = re.sub(r"(\'s)", " is", x)
    x = re.sub(r"(\'d)", " would", x)
    x = re.sub(r"(\'m)", " am", x)
    x = re.sub(r"[']", "", x)
    x = re.sub(r"  ", " ", x)
    x = re.sub(r"\[", "", x)
    x = re.sub(r"\]", "", x)
    
    return x

df.text = df.text.apply(lambda x: replacements(x))

In [5]:
sentences = df.text.tolist()
tokens = [t for t in ''.join(df.text.tolist()).split(' ')]
vocab = list(np.unique(tokens))
word2idx = lambda v: [[v.index(n) for n in sentence.split(' ') if (n in v)] for sentence in sentences] 
nums = word2idx(vocab)
nums = [i[:32] for i in nums]
nums = [j for sub in nums for j in sub]

In [6]:
sl = 32

def create_tuples(nums):
    return L((tensor(nums[i:i+sl]), tensor(nums[i+1:i+sl+1]))
         for i in range(0,len(nums)-sl-1,sl))

def train_test_split(sequences):
    train_size = int(len(sequences) * 0.8)
    train, test = sequences[:train_size], sequences[train_size:]
    return train, test

In [7]:
dset = create_tuples(nums)
train_ds, valid_ds = train_test_split(dset)

In [8]:
train_ds

(#799) [(tensor([17469,  1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895,
        17828, 12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,
         6690,  7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993,
        18233, 16812]), tensor([ 1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895, 17828,
        12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,  6690,
         7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993, 18233,
        16812, 16886])),(tensor([16886,  8934,   301,  6136, 18341, 10158,  6439, 16812,   445, 14683,
          877,  2582, 18618,  1088,   717,  6501, 13438, 16812, 11168,  8934,
         7276, 17083, 16899,  8982,  8934, 11051,  5409,  8467, 16812,  6439,
        18387, 16872]), tensor([ 8934,   301,  6136, 18341, 10158,  6439, 16812,   445, 14683,   877,
         2582, 18618,  1088,   717,  6501, 13438, 16812, 11168,  8934,  7276,
        17083, 16899,  8982,  8934, 11051,  5409,  8467, 168

In [9]:
def reorder_dataset(dataset):
    m = len(dataset) // 64
    print(m)
    new_dset = []
    for i in range(64):
        for j in range(m):
            t = dataset[i+j*64]
            new_dset.append(t)
        print(new_dset)
    return new_dset

In [10]:
train_ds_reordered = reorder_dataset(train_ds)
valid_ds_reordered = reorder_dataset(valid_ds)

12
[(tensor([17469,  1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895,
        17828, 12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,
         6690,  7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993,
        18233, 16812]), tensor([ 1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895, 17828,
        12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,  6690,
         7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993, 18233,
        16812, 16886])), (tensor([12589, 15559, 16041,  1789, 16010,  6857,   445,  8467,   978, 11092,
        18694, 16812, 16172,  7862, 18694, 18797,  9935,  3677,  5915,  8278,
         7760,  7321, 11012,  9618,  7260, 17036,   301,  6903, 16834,  8278,
         7760, 18255]), tensor([15559, 16041,  1789, 16010,  6857,   445,  8467,   978, 11092, 18694,
        16812, 16172,  7862, 18694, 18797,  9935,  3677,  5915,  8278,  7760,
         7321, 11012,  9618,  7260, 17036,   301,  6903, 16834,

[(tensor([17469,  1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895,
        17828, 12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,
         6690,  7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993,
        18233, 16812]), tensor([ 1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895, 17828,
        12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,  6690,
         7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993, 18233,
        16812, 16886])), (tensor([12589, 15559, 16041,  1789, 16010,  6857,   445,  8467,   978, 11092,
        18694, 16812, 16172,  7862, 18694, 18797,  9935,  3677,  5915,  8278,
         7760,  7321, 11012,  9618,  7260, 17036,   301,  6903, 16834,  8278,
         7760, 18255]), tensor([15559, 16041,  1789, 16010,  6857,   445,  8467,   978, 11092, 18694,
        16812, 16172,  7862, 18694, 18797,  9935,  3677,  5915,  8278,  7760,
         7321, 11012,  9618,  7260, 17036,   301,  6903, 16834,  8

[(tensor([17469,  1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895,
        17828, 12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,
         6690,  7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993,
        18233, 16812]), tensor([ 1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895, 17828,
        12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,  6690,
         7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993, 18233,
        16812, 16886])), (tensor([12589, 15559, 16041,  1789, 16010,  6857,   445,  8467,   978, 11092,
        18694, 16812, 16172,  7862, 18694, 18797,  9935,  3677,  5915,  8278,
         7760,  7321, 11012,  9618,  7260, 17036,   301,  6903, 16834,  8278,
         7760, 18255]), tensor([15559, 16041,  1789, 16010,  6857,   445,  8467,   978, 11092, 18694,
        16812, 16172,  7862, 18694, 18797,  9935,  3677,  5915,  8278,  7760,
         7321, 11012,  9618,  7260, 17036,   301,  6903, 16834,  8

[(tensor([17469,  1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895,
        17828, 12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,
         6690,  7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993,
        18233, 16812]), tensor([ 1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895, 17828,
        12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,  6690,
         7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993, 18233,
        16812, 16886])), (tensor([12589, 15559, 16041,  1789, 16010,  6857,   445,  8467,   978, 11092,
        18694, 16812, 16172,  7862, 18694, 18797,  9935,  3677,  5915,  8278,
         7760,  7321, 11012,  9618,  7260, 17036,   301,  6903, 16834,  8278,
         7760, 18255]), tensor([15559, 16041,  1789, 16010,  6857,   445,  8467,   978, 11092, 18694,
        16812, 16172,  7862, 18694, 18797,  9935,  3677,  5915,  8278,  7760,
         7321, 11012,  9618,  7260, 17036,   301,  6903, 16834,  8

[(tensor([17469,  1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895,
        17828, 12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,
         6690,  7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993,
        18233, 16812]), tensor([ 1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895, 17828,
        12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,  6690,
         7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993, 18233,
        16812, 16886])), (tensor([12589, 15559, 16041,  1789, 16010,  6857,   445,  8467,   978, 11092,
        18694, 16812, 16172,  7862, 18694, 18797,  9935,  3677,  5915,  8278,
         7760,  7321, 11012,  9618,  7260, 17036,   301,  6903, 16834,  8278,
         7760, 18255]), tensor([15559, 16041,  1789, 16010,  6857,   445,  8467,   978, 11092, 18694,
        16812, 16172,  7862, 18694, 18797,  9935,  3677,  5915,  8278,  7760,
         7321, 11012,  9618,  7260, 17036,   301,  6903, 16834,  8

...

[(tensor([17469,  1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895,
        17828, 12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,
         6690,  7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993,
        18233, 16812]), tensor([ 1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895, 17828,
        12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,  6690,
         7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993, 18233,
        16812, 16886])), (tensor([12589, 15559, 16041,  1789, 16010,  6857,   445,  8467,   978, 11092,
        18694, 16812, 16172,  7862, 18694, 18797,  9935,  3677,  5915,  8278,
         7760,  7321, 11012,  9618,  7260, 17036,   301,  6903, 16834,  8278,
         7760, 18255]), tensor([15559, 16041,  1789, 16010,  6857,   445,  8467,   978, 11092, 18694,
        16812, 16172,  7862, 18694, 18797,  9935,  3677,  5915,  8278,  7760,
         7321, 11012,  9618,  7260, 17036,   301,  6903, 16834,  8

[(tensor([17469,  1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895,
        17828, 12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,
         6690,  7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993,
        18233, 16812]), tensor([ 1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895, 17828,
        12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,  6690,
         7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993, 18233,
        16812, 16886])), (tensor([12589, 15559, 16041,  1789, 16010,  6857,   445,  8467,   978, 11092,
        18694, 16812, 16172,  7862, 18694, 18797,  9935,  3677,  5915,  8278,
         7760,  7321, 11012,  9618,  7260, 17036,   301,  6903, 16834,  8278,
         7760, 18255]), tensor([15559, 16041,  1789, 16010,  6857,   445,  8467,   978, 11092, 18694,
        16812, 16172,  7862, 18694, 18797,  9935,  3677,  5915,  8278,  7760,
         7321, 11012,  9618,  7260, 17036,   301,  6903, 16834,  8

[(tensor([17469,  1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895,
        17828, 12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,
         6690,  7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993,
        18233, 16812]), tensor([ 1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895, 17828,
        12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,  6690,
         7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993, 18233,
        16812, 16886])), (tensor([12589, 15559, 16041,  1789, 16010,  6857,   445,  8467,   978, 11092,
        18694, 16812, 16172,  7862, 18694, 18797,  9935,  3677,  5915,  8278,
         7760,  7321, 11012,  9618,  7260, 17036,   301,  6903, 16834,  8278,
         7760, 18255]), tensor([15559, 16041,  1789, 16010,  6857,   445,  8467,   978, 11092, 18694,
        16812, 16172,  7862, 18694, 18797,  9935,  3677,  5915,  8278,  7760,
         7321, 11012,  9618,  7260, 17036,   301,  6903, 16834,  8

[(tensor([17469,  1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895,
        17828, 12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,
         6690,  7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993,
        18233, 16812]), tensor([ 1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895, 17828,
        12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,  6690,
         7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993, 18233,
        16812, 16886])), (tensor([12589, 15559, 16041,  1789, 16010,  6857,   445,  8467,   978, 11092,
        18694, 16812, 16172,  7862, 18694, 18797,  9935,  3677,  5915,  8278,
         7760,  7321, 11012,  9618,  7260, 17036,   301,  6903, 16834,  8278,
         7760, 18255]), tensor([15559, 16041,  1789, 16010,  6857,   445,  8467,   978, 11092, 18694,
        16812, 16172,  7862, 18694, 18797,  9935,  3677,  5915,  8278,  7760,
         7321, 11012,  9618,  7260, 17036,   301,  6903, 16834,  8

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [11]:
print(train_ds_reordered)

[(tensor([17469,  1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895,
        17828, 12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,
         6690,  7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993,
        18233, 16812]), tensor([ 1987,  1762, 10575, 14370,  5078, 11507,  5915,  9981,  7895, 17828,
        12362, 10032, 14785,  8467, 16886, 18397, 11491, 10220, 10523,  6690,
         7895, 14953, 16961,   445, 14611,  7693, 17036,  1764, 14993, 18233,
        16812, 16886])), (tensor([12589, 15559, 16041,  1789, 16010,  6857,   445,  8467,   978, 11092,
        18694, 16812, 16172,  7862, 18694, 18797,  9935,  3677,  5915,  8278,
         7760,  7321, 11012,  9618,  7260, 17036,   301,  6903, 16834,  8278,
         7760, 18255]), tensor([15559, 16041,  1789, 16010,  6857,   445,  8467,   978, 11092, 18694,
        16812, 16172,  7862, 18694, 18797,  9935,  3677,  5915,  8278,  7760,
         7321, 11012,  9618,  7260, 17036,   301,  6903, 16834,  8

In [12]:
dls = DataLoaders.from_dsets(
    train_ds_reordered,
    valid_ds_reordered,
    bs=64, drop_last=True, shuffle=False
)

### 4b (10 points). Implement a 2-layer LSTM Language Model that has:
- One dropout layer (with 50% chance)
- Weight tying between the input and output embedding layers
- Activation regularization
- Temporal activation regularization

You can use anything, such as the LSTM module from pytorch.

In [16]:
bs = 64
class LMModel6(Module):
    def __init__(self, vocab_sz, n_hidden, n_layers):
        self.i_h = nn.Embedding(vocab_sz, n_hidden)
        self.rnn = nn.LSTM(n_hidden, n_hidden, n_layers, batch_first=True)
        self.h_o = nn.Linear(n_hidden, vocab_sz)
        self.h = [torch.zeros(n_layers, bs, n_hidden) for _ in range(2)]
        
    def forward(self, x):
        self.res,h = self.rnn(self.i_h(x), self.h)
        self.h = [h_.detach() for h_ in h]
        return self.h_o(self.res)
    
    def reset(self): 
        for h in self.h: h.zero_()

In [25]:
class MyRNNRegularizer(Callback):
    def __init__(self, alpha=0., beta=0.): self.alpha, self.beta = alpha, beta

    # This is called after the forward pass of the model
    def after_pred(self):
        # Store inside this class the raw output of the model and the dropped out output, respectively 
        self.raw, self.out = self.h, self.h_o
        # Modify the model's output to be just the activation of the last layer
        self.learn.pred = self.h_o(self.res)

    # This is called after the normal loss is computed
    def after_loss(self):
        if not self.training: return
        if self.alpha != 0.:
            print(self.learn.loss)
            self.learn.loss += self.alpha * (sum(self.h)/len(self.h)).pow(2)
#         if self.beta != 0.:
#             self.learn.loss += self.beta * (self.h[:,1:] - self.h[:,:-1]).pow(2).mean()

In [26]:
learn = Learner(dls, LMModel6(len(vocab), 64, 2), 
                loss_func=CrossEntropyLossFlat(), 
                metrics=accuracy, cbs=[ModelResetter, MyRNNRegularizer(alpha=2, beta=1)])
learn.fit_one_cycle(15, 1e-2)

TensorBase(9.8582, grad_fn=<AliasBackward0>)


RuntimeError: Exception occured in `MyRNNRegularizer` when calling event `after_loss`:
	output with shape [] doesn't match the broadcast shape [2, 64, 64]

### 4c (5 points). Find the best learning rate and train your NN with 1cycle policy and Adam. Report your result with a reasonable metric.